# BEE 4750 Homework 3: Uncertain Sea-Level Rise and Levee Reliability

**Name**:

**ID**:

> **Due Date**
>
> Friday, 10/06/23, 9:00pm

## Overview

### Instructions

This assignment asks you to conduct a Monte Carlo analysis of levee
reliability in the face of uncertain changes to local sea levels. You
will propagate uncertainty in equilibrium climate sensitivity through
the energy balance model to obtain a distribution of temperatures, which
will then drive a model of sea-level rise. You will finally use this
distribution to assess the probability that a planned levee will achieve
its desired reliability standard.

### Load Environment

The following code loads the environment and makes sure all needed
packages are installed. This should be at the start of most Julia
scripts.

In [1]:
import Pkg
Pkg.activate(@__DIR__)
Pkg.instantiate()

In [1]:
using Random
using Plots
using LaTeXStrings
using Distributions
using CSV
using DataFrames

## Problems (Total: 40 Points)

### Problem 1 (12 points)

Recall from class that the simple energy balance model (EBM) of
planetary energy balance links changes in radiative forcing ($F$) to
global mean temperature ($T$) changes through the discretized equation
$$T_{i+1} = T_{i} + \frac{F_i - \lambda T_i}{cd} \times \Delta t,$$
where $i$ is the current time step, $c = 4.184 \times 10^6$
J/K/m<sup>2</sup> is the heat capacity of water per unit area, $d$ is
the (uncertain) depth of the mixing layer, $\Delta t$ is the annual time
step in seconds and $\lambda = F_{\text{2xCO}_2}/S$ is the climate
feedback parameter in W/m<sup>2</sup>/$^\circ$ C, where $S$ is the
equilibrium climate sensitivity (the uncertain equilibrium temperature
change resulting from a doubling of atmospheric CO<sub>2</sub>).
Finally, while total radiative forcing can be the result of non-aerosol
and aerosol effects, we do not know the relative intensity of aerosol
forcing, so we represent this with an uncertain aerosol scaling factor
$\alpha$.

We can implement this model with the following Julia function. We will
assume an ocean mixing depth $d = 100$ m and an aerosol scaling factor
$\alpha = 1.3$ so we can focus on the uncertainty in $S$.

The last technical concern is that “global mean temperature” does not
make sense in absolute terms as a marker of climate change. Instead, we
typically refer to temperature changes relative to some historical
pre-industrial baseline. In this case, we will use the period from
1880-1900, though this choice can vary.

In [1]:
# we need to split up the aerosol and non-aerosol forcings when we call the function
function energy_balance_model(S, forcing_aerosol, forcing_non_aerosol)
    d = 100 # ocean mixing depth [m]
    α = 1.3 # aerosol scaling factor
    F2xCO₂ = 4.0 # radiative forcing [W/m²] for a doubling of CO₂
    λ = F2xCO₂/S
    
    c = 4.184e6 # heat capacity/area [J/K/m²]
    C = c*d # heat capacity of mixed layer (per area)

    F = forcing_non_aerosol + α*forcing_aerosol # radiative forcing

    Δt = 31558152.0 # annual timestep [s]
    
    T = zero(F)
    for i in 1:length(F)-1
        T[i+1] = T[i] + (F[i] - λ*T[i])/C * Δt
    end
    # return temperature anomaly relative to 1880-1900 baseline
    return T .- mean(T[1:21]) 
end

energy_balance_model (generic function with 1 method)

Finally, we need to load some radiative forcing data. We will use the
radiative forcing scenario RCP 8.5. We can load this data, which is in a
`.csv` (comma-delimited) file, into a `DataFrame`, which is a tabular
data structure. Rows and columns in a `DataFrame` can be accessed using
their numerical index (like a matrix), but columns also have names; you
can access a particular column in a dataframe `df` by name using
`df.colname` or `df[:, "colname"]`.

Of note: this data set goes from 1750–2500, so you will need to take
care to make sure you are using the right years at each step. For
example, here we will constrain the data to 1880–2100, which is the
period we are interested in.

In [1]:
# The CSV is read into a DataFrame object, and we specify that it is comma delimited
forcings_all_85 = CSV.read("data/ERF_ssp585_1750-2500.csv", DataFrame, delim=",")

# get the years corresponding to the forcings
t = Int64.(forcings_all_85[!,"year"]) # Ensure that years are interpreted as integers
# find the indices of the years 1880 and 2100
# we can do this with the indexin function
time_bounds = indexin([1880, 2100], t)
years = time_bounds[1]:time_bounds[2] # create range of years

# Separate out the individual components
forcing_co2_85 = forcings_all_85[years,"co2"]
# Get total aerosol and non-aerosol forcings
forcing_aerosol_rad_85 = forcings_all_85[years,"aerosol-radiation_interactions"]
forcing_aerosol_cloud_85 = forcings_all_85[years,"aerosol-cloud_interactions"]
forcing_aerosol_85 = forcing_aerosol_rad_85 + forcing_aerosol_cloud_85 # aerosol forcings
forcing_total_85 = forcings_all_85[years,"total"] 
forcing_non_aerosol_85 = forcing_total_85 - forcing_aerosol_85 # non-aerosol forcings


221-element Vector{Float64}:
  0.42741479112315905
  0.4487940147601447
  0.4900144276528058
 -0.019811270078689047
 -1.480725700367619
 -0.3154905163510021
  0.233186559774844
  0.2923308952663089
  0.45833872365810924
  0.5168189581089915
  ⋮
  9.879065698371564
  9.946850640754889
 10.002169546141578
 10.061009359425011
 10.115684195707905
 10.182946497594184
 10.249699157847772
 10.331407709334023
 10.424544495740134

For this assignment, you can use the `forcing_aerosol_85` and
`forcing_non_aerosol_85` vectors as is to correspond to the relevant
forcings. You will need to use the vector `t` to find the appropriate
years for analysis.

#### Problem 1.1 (3 points)

Assume that $S$ is distributed according to
$\text{LogNormal}(\log(3.2), \log{2}/3)$ (as in class). Draw 10,000
samples from this distribution and make a histogram.

#### Problem 1.2 (5 points)

Use the EBM to propagate your samples of $S$ to a distribution of global
mean temperature. Plot the median and 90% predictive distribution
(between the .05 and .95 quantiles) from 1880-2100.

#### Problem 1.3 (4 points)

Make a histogram of global mean temperature projections in 2100. If you
compare this distribution to the distribution of $S$ from Problem 1.1,
what do you observe?

### Problem 2 (15 points)

Changes to global temperatures cause changes in global sea levels
through several mechanisms, including thermal expansion (the change in
ocean volume due to increased heat content) and melting land-based ice.
One simple way to represent this link is through the following model,
proposed by [Rahmstorf (2007)](https://doi.org/10.1126/science.1135456).

$$\frac{dH}{dt} = a(T-T_0),$$

where $H$ is the global mean sea level in mm, $T$ is global mean
temperature, $T_0$ is an equilibrium temperature (where there is no
change in sea levels), and $a$ is a proportionality constant. This model
can be discretized to give $$H_{i+1} - H_i = a (T_i - T_0).$$

Note that, like with global mean temperature, the notion of “global mean
sea level” does not make sense in absolute terms (were sea levels ever
at “zero”?). Instead, we want to normalize this relative to some
historical baseline. In this case (with a view towards Problem 3), we
will compute our sea levels relative to the 2010 sea level. Note that in
addition to the model parameters, we also need an initial sea-level
parameter $H_0$ which will give us the right anomaly level.

The best estimates for these parameters are:

-   $a = 1.86$;
-   $H_0 = -223$;
-   $T_0 = -0.62$

#### Problem 2.1 (5 points)

Write a function `sea_level_model()` to implement the mathematical
sea-level rise model described above. It should take in needed
parameters and a vector of temperatures and return a vector of sea
levels. To test your function, use the provided temperature series
`historical_temps` (read in below) to compute the global mean sea level
anomaly in 2022 (the last year of the dataset) with the parameter values
above; you should get a value of approximately 40mm.

In [1]:
historical_temp_data = CSV.read("data/HadCRUT.5.0.1.0.analysis.summary_series.global.annual.csv", DataFrame, delim=",")
# column 2 is the temperature anomaly, column 1 is the year
temp_bds = indexin([1880, 1900], historical_temp_data[!, 1]) # find the index of 2010 for normalization
historical_temp_data[:, 2] .-= mean(historical_temp_data[temp_bds[1]:temp_bds[2], 2])
historical_temps = historical_temp_data[temp_bds[1]:end, 2]

143-element Vector{Float64}:
  0.07297116761904765
  0.15655772761904765
  0.09327316761904769
  0.04232884761904765
 -0.10351681238095234
 -0.08232033238095232
 -0.03210037238095231
 -0.10998251238095236
  0.00942435761904764
  0.13890768761904768
  ⋮
  1.0616748976190478
  1.2139176176190476
  1.3217303776190477
  1.2339774976190476
  1.1514572476190477
  1.2798758476190477
  1.3115970476190477
  1.1506591476190478
  1.1896871476190476

#### Problem 2.2 (5 points)

Evaluate `sea_level_model()` using the projected temperature ensemble
from Problem 1. Plot the 90% projection interval of the sea levels.

#### Problem 2.3 (5 points)

Make a histogram of the sea-level anomaly in 2100. What can you observe
about how the ECS uncertainty has impacted sea-level uncertainty under
this radiative forcing scenario? What might the implications be of only
using the best-estimate ECS value?

### Problem 3 (13 points)

You’ve been asked to consult on a levee reliability analysis. For
context, levees in the United States are supposed to only fail once in
100 years, or, in other words, to have at most a 1% chance of failure in
a given year. We will assume for this problem that the only way in which
a levee fails is by being overtopped (note: this is unrealistic).

We can assess the probability of levee overtopping by comparing its
height to a distribution of extreme sea levels. A common approach is to
look at the distribution of the highest sea level each year. These
extreme sea levels can be obtained by combining the absolute sea level
(we will use our distribution of global sea levels for this), the rate
of subsidence (how much the ground sinks), and the distribution of storm
tides (the highest tide level, which is often the result of storm surges
combining with high tide).

Assume for this problem that:

1.  the annual rate of subsidence $\nu$ is 1.2mm/yr;
2.  the distribution of annual storm tide maxima, above the mean sea
    level, is (and is expected to continue to be) given by a
    $\text{GeneralizedExtremeValue}(900, 25, 0.3)$ distribution, which
    looks like this:

In [1]:
tide_distribution = GeneralizedExtremeValue(900, 25, 0.3)
    histogram(rand(tide_distribution, 10000), xlabel="Storm Tide Height (mm)", ylabel="Count", legend=:false)

<?xml version="1.0" encoding="utf-8"?>
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 
 <path clip-path="url(#clip110)" d="M607.085 1767.34 Q603.473 1767.34 601.645 1770.9 Q599.839 1774.45 599.839 1781.58 Q599.839 1788.68 601.645 1792.25 Q603.473 1795.79 607.085 1795.79 Q610.719 1795.79 612.524 1792.25 Q614.353 1788.68 614.353 1781.58 Q614.353 1774.45 612.524 1770.9 Q610.719 1767.34 607.085 1767.34 M607.085 1763.64 Q612.895 1763.64 615.95 1768.24 Q619.029 1772.83 619.029 1781.58 Q619.029 1790.3 615.95 1794.91 Q612.895 1799.49 607.085 1799.49 Q601.274 1799.49 598.196 1794.91 Q595.14 1790.3 595.14 1781.58 Q595.14 1772.83 598.196 1768.24 Q601.274 1763.64 607.085 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip110)" d="M637.246 1767.34 Q633.635 1767.34 631.807 1770.9 Q630.001 1774.45 630.001 1781.58 Q630.001 1788.68 631.807 1792.25 Q633.635 1795.79 637.246 1795.79 Q640.881 1795.79 642.686 1792.25 Q644.515 1788.68 644.515 1781.58 Q644.515 1774.45 642.686 1770.9 Q640.881 1767.34 637.246 1767.34 M637.246 1763.64 Q643.057 1763.64 646.112 1768.24 Q649.191 1772.83 649.191 1781.58 Q649.191 1790.3 646.112 1794.91 Q643.057 1799.49 637.246 1799.49 Q631.436 1799.49 628.358 1794.91 Q625.302 1790.3 625.302 1781.58 Q625.302 1772.83 628.358 1768.24 Q631.436 1763.64 637.246 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip110)" d="M667.408 1767.34 Q663.797 1767.34 661.969 1770.9 Q660.163 1774.45 660.163 1781.58 Q660.163 1788.68 661.969 1792.25 Q663.797 1795.79 667.408 1795.79 Q671.043 1795.79 672.848 1792.25 Q674.677 1788.68 674.677 1781.58 Q674.677 1774.45 672.848 1770.9 Q671.043 1767.34 667.408 1767.34 M667.408 1763.64 Q673.218 1763.64 676.274 1768.24 Q679.353 1772.83 679.353 1781.58 Q679.353 1790.3 676.274 1794.91 Q673.218 1799.49 667.408 1799.49 Q661.598 1799.49 658.519 1794.91 Q655.464 1790.3 655.464 1781.58 Q655.464 1772.83 658.519 1768.24 Q661.598 1763.64 667.408 1763.64 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /> <path clip-path="url(#clip110)" d="M1031.61 1794.89 L1047.93 1794.89 L1047.93 1798.82 L1025.99 1798.82 L1025.99 1794.89 Q1028.65 1792.13 1033.23 1787.5 Q1037.84 1782.85 1039.02 1781.51 Q1041.26 1778.98 1042.14 1777.25 Q1043.05 1775.49 1043.05 1773.8 Q1043.05 1771.04 1041.1 1769.31 Q1039.18 1767.57 1036.08 1767.57 Q1033.88 1767.57 1031.43 1768.34 Q1029 1769.1 1026.22 1770.65 L1026.22 1765.93 Q1029.04 1764.79 1031.5 1764.21 Q1033.95 1763.64 1035.99 1763.64 Q1041.36 1763.64 1044.55 1766.32 Q1047.75 1769.01 1047.75 1773.5 Q1047.75 1775.63 1046.94 1777.55 Q1046.15 1779.45 1044.04 1782.04 Q1043.46 1782.71 1040.36 1785.93 Q1037.26 1789.12 1031.61 1794.89 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip110)" d="M1057.79 1764.26 L1076.15 1764.26 L1076.15 1768.2 L1062.07 1768.2 L1062.07 1776.67 Q1063.09 1776.32 1064.11 1776.16 Q1065.13 1775.97 1066.15 1775.97 Q1071.94 1775.97 1075.32 1779.15 Q1078.7 1782.32 1078.7 1787.73 Q1078.7 1793.31 1075.22 1796.41 Q1071.75 1799.49 1065.43 1799.49 Q1063.26 1799.49 1060.99 1799.12 Q1058.74 1798.75 1056.33 1798.01 L1056.33 1793.31 Q1058.42 1794.45 1060.64 1795 Q1062.86 1795.56 1065.34 1795.56 Q1069.34 1795.56 1071.68 1793.45 Q1074.02 1791.34 1074.02 1787.73 Q1074.02 1784.12 1071.68 1782.02 Q1069.34 1779.91 1065.34 1779.91 Q1063.46 1779.91 1061.59 1780.33 Q1059.74 1780.74 1057.79 1781.62 L1057.79 1764.26 Z" fill="#000000" fill-rule="nonzero" fill-opacity="1" /><path clip-path="url(#clip110)" d="M1097.91 1767.34 Q1094.3 1767.34 1092.47 1770.9 Q1090.66 1774.45 1090.66 1781.58 Q1090.66 1788.68 1092.47 1792.25 Q1094.3 1795.79 1097.91 1795.79 Q1101.54 1795.79 1103.35 1792.25 Q1105.18 1788.68 1105.18 1781.58 Q1105.18 1774.45 1103.35 1770.9 Q1101.54 1767.34 1097.91 1767.34 M1097.91 1763.64 Q1103.72 1763.64 1106.77 1768.24 Q1109.85 1772.83 1109.85 1781.58 Q1109.85 1790.3 1106.77 1794.91 Q1103.72 1799.49 1097.91 1799.49 Q1092.1 1799.49 1089.02 1794.91 Q1085.96 179

Feel free to just sample from `tide_distribution` in your solution
below.

#### Problem 3.1 (2 points)

How would you use your sea-level simulations and the above information
to compute a distribution of extreme sea levels in 2100 relative to 2010
mean sea level? Write down the approach in clear steps, with equations
as needed.

#### Problem 3.2 (3 points)

Follow the steps above and produce a histogram of the extreme sea levels
in 2100 relative to 2010.

#### Problem 3.3 (5 points)

The current levee was heightened in 2010 to 2m above the 2010 mean sea
level. Based on your analysis above, what is the probability that the
levee will be overtopped in 2100 (remember that the reliability standard
is 1%)?

#### Problem 3.4 (3 points)

Based on your analysis, would you recommend that the levee be heightened
again in the future, and if so, how high? What other information might
you need, if any, to make your recommendation?

## References

List any external references consulted, including classmates.